In [214]:
# Look at breweries


# Preprocess

In [215]:
import pandas as pd
import numpy as np

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

import os

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

### Import data

#### Venue Data

In [216]:
# Zip code venue data part 1
url = 'https://raw.githubusercontent.com/vjacobsen/Coursera_Capstone/master/Dataset_zips_1.csv'
zips_1 = pd.read_csv(url, error_bad_lines=False)

# Zip code venue data part 2
url = 'https://raw.githubusercontent.com/vjacobsen/Coursera_Capstone/master/Dataset_zips_2.csv'
zips_2 = pd.read_csv(url, error_bad_lines=False)

# Append zip 1 and zip 2 dataframes
cities_zips = zips_1.append(zips_2)
cities_zips = cities_zips.rename(columns={'zip_latitute':'zip_latitude'})

# Convert Zip to string
cities_zips['zip_code'] = cities_zips['zip_code'].astype(str)

# Format Zip code
# pad to 5 chars 
cities_zips['zip_code'] = [string.replace('.0','') for string in cities_zips['zip_code'].astype(str)]
cities_zips['zip_code'] = cities_zips['zip_code'].str.pad(5,side='left',fillchar='0')

print(cities_zips.shape)
cities_zips.sample(5)

(298390, 8)


zip_code  zip_latitude  zip_longitude  \
91570     20537     38.894097     -77.025133   
74323     27519     35.768120     -78.829548   
155218    80904     38.850558    -104.864810   
145159    90806     33.801767    -118.185800   
72467     93901     36.665879    -121.654970   

                                         venue                  venue_id  \
91570   Dinosaurs/Hall of Paleobiology Exhibit  4d695be4342b8cfaa7d6c72c   
74323                     Bond Park Lake Trail  4e1f8f43fa761d67106951b8   
155218                           The UPS Store  4d4326eab6e73704a32c8d09   
145159                        Ten Mile Brewing  59aa1fe1aa6c95709b254360   
72467                         The Salad Shoppe  4c114383a9420f473c747c51   

        venue_latitude  venue_longitude  venue_category  
91570        38.891190       -77.026325  Science Museum  
74323        35.780872       -78.825127           Trail  
155218       38.853009      -104.873460  Shipping Store  
145159       33.803971      -118.177832         Brewery  
72467        36.660220      -121.659819     Salad Place

#### Census Data

In [217]:
acs_features = pd.read_feather('Dataset_census_features.feather')
acs_features = acs_features.set_index('zip_code')
acs_features.sample(5)

Estimate!!INCOME AND BENEFITS (IN 2018 INFLATION-ADJUSTED DOLLARS)!!Total households!!Median household income (dollars)  \
zip_code                                                                                                                            
50065                                               31023.0                                                                         
55437                                               72284.0                                                                         
28017                                               51913.5                                                                         
85743                                               72353.0                                                                         
98108                                               55314.0                                                                         

          Estimate!!COMMUTING TO WORK!!Workers 16 years and over!!Mean travel time to work (minutes)  \
zip_code                                                                                               
50065                                                  39.3                                            
55437                                                  20.5                                            
28017                                                  11.2                                            
85743                                                  31.0                                            
98108                                                  28.9                                            

          Percent Estimate!!EMPLOYMENT STATUS!!Civilian labor force!!Unemployment Rate  \
zip_code                                                                                 
50065                                                   5.6                              
55437                                                   2.4                              
28017                                                  22.5                              
85743                                                   6.1                              
98108                                                   9.1                              

          Estimate!!GROSS RENT!!Occupied units paying rent!!Median (dollars)  \
zip_code                                                                       
50065                                                 773.0                    
55437                                                1106.0                    
28017                                                 773.0                    
85743                                                1225.0                    
98108                                                1097.0                    

          Percent Estimate!!SEX AND AGE!!Total population!!Male  \
zip_code                                                          
50065                                                  47.3       
55437                                                  48.9       
28017                                                  32.7       
85743                                                  48.7       
98108                                                  51.4       

          Percent Estimate!!SEX AND AGE!!Total population!!Female  \
zip_code                                                            
50065                                                  52.7         
55437                                                  51.1         
28017                                                  67.3         
85743                                                  51.3         
98108                                                  48.6         

          Estimate!!SEX AND AGE!!Total population!!Median age (years)  \
zip_code                                                                
50065                                                  34

### Remove Duplicates

When pulling zip data from Foursquare, some venues might have duplicated due to overlapping radius between two zip codes. We need to check and remove duplicate venues

In [218]:
print('Original number of duplicate venues: ',  len(cities_zips['venue_id']) - len(cities_zips['venue_id'].unique()))

# Filter data to only zips contained in Census data
cities_zips = cities_zips[cities_zips['zip_code'].isin(acs_features.index)]

print('Within acs_features: ',  len(cities_zips['venue_id']) - len(cities_zips['venue_id'].unique()))

# Drop dupl
cities_zips = cities_zips.drop_duplicates(subset=['venue_id'])

print('After dropping dup venue id:: ',  len(cities_zips['venue_id']) - len(cities_zips['venue_id'].unique()))

Original number of duplicate venues:  138571
Within acs_features:  25217
After dropping dup venue id::  0


Add city data back to venuesand zips

In [219]:
# Import city data
city_data = pd.read_csv('Dataset_Top_100_Cities_Zip.csv',dtype={'Zip':str})

# Format Zip code, pad to 5 chars 
city_data['Zip'] = [string.replace('.0','') for string in city_data['Zip'].astype(str)]
city_data['Zip'] = city_data['Zip'].str.pad(5,side='left',fillchar='0')

city_data.sample(5)

PopRank           City       State  city_pop_2013  Pop2010  \
5261      108         Oxnard  California         203007   197899   
2412       27  Oklahoma City    Oklahoma         610613   579999   
5889      140     Santa Rosa  California         171990   167815   
2370       27  Oklahoma City    Oklahoma         610613   579999   
2908       35     Sacramento  California         479686   466488   

      city_pop_chg_pcnt ChangePercent   SqMi  city_pop_sqmi  city_longitude  \
5261               2.58        0 to 5   26.9           7358         34.2023   
2412               5.28       5 to 10  606.4            956         35.4671   
5889               2.49        0 to 5   41.3           4064         38.4468   
2370               5.28       5 to 10  606.4            956         35.4671   
2908               2.83        0 to 5   97.9           4764         38.5666   

      city_latitude    Zip   Latitude   Longitude  Timezone  \
5261      -119.2046  93033  34.166933 -119.161130      -8.0   
2412       -97.5137  73127  35.481507  -97.642300      -6.0   
5889      -122.7061  95408  38.463088 -122.989975      -8.0   
2370       -97.5137  73139  35.388461  -97.527130      -6.0   
2908      -121.4686  95827  38.566506 -121.325150      -8.0   

      Daylight savings time flag               geopoint  state_name  
5261                         1.0   34.166933,-119.16113  California  
2412                         1.0     35.481507,-97.6423    Oklahoma  
5889                         1.0  38.463088,-122.989975  California  
2370                         1.0    35.388461,-97.52713    Oklahoma  
2908                         1.0   38.566506,-121.32515  California

In [220]:
# Add City to venue data
venues_cities = cities_zips.merge(city_data[['Zip','City','State']],left_on=['zip_code'], right_on=['Zip'],how='left')
venues_cities.sample(5)

zip_code  zip_latitude  zip_longitude                          venue  \
67822     33168     25.892185      -80.21032              La Primera Parada   
104473    28305     35.056963      -78.90369            Fire Protection Inc   
110258    84101     40.754746     -111.89875  Moochie's Meatballs and More!   
31050     94123     37.801028     -122.43836                         Flores   
1353      10023     40.776099      -73.98285               Ladies' Pavilion   

                        venue_id  venue_latitude  venue_longitude  \
67822   4d2ca48577a2a1cd0c5687b7       25.882946       -80.214775   
104473  566c752f498ec5ed8de324e7       35.066414       -78.898825   
110258  4b70b200f964a520232a2de3       40.751759      -111.884127   
31050   57fc2013498ec2b5a315b412       37.797616      -122.432581   
1353    4b488613f964a520a94e26e3       40.777645       -73.972927   

                   venue_category    Zip            City           State  
67822   Latin American Restaurant  33168           Miami         Florida  
104473             Clothing Store  28305    Fayetteville  North Carolina  
110258             Sandwich Place  84101  Salt Lake City            Utah  
31050          Mexican Restaurant  94123   San Francisco      California  
1353                         Park  10023        New York        New York

In [221]:
from pivottablejs import pivot_ui
#pivot_ui(venues_cities)

For the purpose of this project, we are analysing a specific category: Beerhouses/bars/breweries. Let's have a look at the total number of venues under each category.

In [222]:
# Masks
beer_mask = venues_cities['venue_category'].str.contains('Beer')
brewery_mask = venues_cities['venue_category']=='Brewery'

# Value counts
selected_cat = venues_cities[brewery_mask | beer_mask]['venue_category'].value_counts().to_frame()
selected_cat

venue_category
Brewery                1028
Beer Garden             207
Beer Bar                158
Beer Store              103

We will replace all of these categories with a single category called  "Beer Venue"

In [223]:
# Create mapping dict
selected_cat['new_cat'] = 'Beer Venue'
mapping_dict = selected_cat['new_cat'].to_dict()

# Replace values in dataframe
venues_cities['venue_category'] = venues_cities['venue_category'].replace(mapping_dict)

### Frequencies of each category relative to each zip total number of categories

In [224]:
# Create a function to get frequency and rank
def category_frequency_func(df,freq=True):
    frequencies = df['venue_category'].value_counts(normalize=freq).to_frame()
    frequencies['rank'] = np.arange(1,len(frequencies)+1)
    frequencies = frequencies.reset_index().rename(columns={'index':'venue_category',
                                              'venue_category':'cat_frequency'})
    return frequencies

# Apply function to each zip
category_frequencies = venues_cities.groupby(['State','City','zip_code']).apply(category_frequency_func)
category_frequencies.index = category_frequencies.index.droplevel(3)
category_frequencies.head()

venue_category  cat_frequency  rank
State   City       zip_code                                          
Alabama Birmingham 35203             Coffee Shop       0.057692     1
                   35203     Fried Chicken Joint       0.057692     2
                   35203                   Hotel       0.057692     3
                   35203                 Theater       0.038462     4
                   35203      Chinese Restaurant       0.038462     5

#### Most common categories by zip

In [225]:
cat_freq_common = category_frequencies.reset_index()

# Number of top categories to get rank
n = 5
cat_freq_common = cat_freq_common[cat_freq_common['rank']<=n]
cat_freq_common = cat_freq_common.set_index('zip_code')
cat_freq_common.head()

State        City       venue_category  cat_frequency  rank
zip_code                                                               
35203     Alabama  Birmingham          Coffee Shop       0.057692     1
35203     Alabama  Birmingham  Fried Chicken Joint       0.057692     2
35203     Alabama  Birmingham                Hotel       0.057692     3
35203     Alabama  Birmingham              Theater       0.038462     4
35203     Alabama  Birmingham   Chinese Restaurant       0.038462     5

In [226]:
# Pivot rank from long to wide
category_rank = cat_freq_common.reset_index().pivot('zip_code','rank','venue_category')

# Rename columns
category_rank.columns = ['rank_'+ str(name) for name in category_rank.columns]
category_rank.head()

rank_1               rank_2            rank_3  \
zip_code                                                                 
01103                Donut Shop  American Restaurant             Hotel   
01104      Fast Food Restaurant          Pizza Place          Pharmacy   
01105            Discount Store  American Restaurant               Gym   
01107            Sandwich Place       Baseball Field  Business Service   
01108     Vietnamese Restaurant                 Park          Pharmacy   

                     rank_4          rank_5  
zip_code                                     
01103           Pizza Place    Burger Joint  
01104            Donut Shop  Discount Store  
01105             Hotel Bar    Liquor Store  
01107     Convenience Store      Donut Shop  
01108           Gas Station   Grocery Store

#### Venue Category Frequency Matrix - Category-Zip Total Relative 

In [227]:
category_frequencies_matrix = category_frequencies.reset_index().pivot('zip_code','venue_category','cat_frequency').fillna(0)
category_frequencies_matrix.head()

venue_category      ATM  Acai House  Accessories Store  Acupuncturist  \
zip_code                                                                
01103           0.00000         0.0                0.0            0.0   
01104           0.00000         0.0                0.0            0.0   
01105           0.00000         0.0                0.0            0.0   
01107           0.00000         0.0                0.0            0.0   
01108           0.03125         0.0                0.0            0.0   

venue_category  Adult Boutique  Advertising Agency  Afghan Restaurant  \
zip_code                                                                
01103                      0.0                 0.0                0.0   
01104                      0.0                 0.0                0.0   
01105                      0.0                 0.0                0.0   
01107                      0.0                 0.0                0.0   
01108                      0.0                 0.0                0.0   

venue_category  African Restaurant  Airport  Airport Food Court  ...  \
zip_code                                                         ...   
01103                          0.0      0.0                 0.0  ...   
01104                          0.0      0.0                 0.0  ...   
01105                          0.0      0.0                 0.0  ...   
01107                          0.0      0.0                 0.0  ...   
01108                          0.0      0.0                 0.0  ...   

venue_category  Whisky Bar  Wine Bar  Wine Shop  Winery  Wings Joint  \
zip_code                                                               
01103                  0.0       0.0        0.0     0.0          0.0   
01104                  0.0       0.0        0.0     0.0          0.0   
01105                  0.0       0.0        0.0     0.0          0.0   
01107                  0.0       0.0        0.0     0.0          0.0   
01108                  0.0       0.0        0.0     0.0          0.0   

venue_category  Women's Store  Xinjiang Restaurant  Yoga Studio  Zoo  \
zip_code                                                               
01103                     0.0                  0.0          0.0  0.0   
01104                     0.0                  0.0          0.0  0.0   
01105                     0.0                  0.0          0.0  0.0   
01107                     0.0                  0.0          0.0  0.0   
01108                     0.0                  0.0          0.0  0.0   

venue_category  Zoo Exhibit  
zip_code                     
01103                   0.0  
01104                   0.0  
01105                   0.0  
01107                   0.0  
01108                   0.0  

[5 rows x 645 columns]

### Number of Venues by category per 1000 people

#### Count of each category relative to each zip

In [228]:
# Apply function to each zip
category_count = venues_cities.groupby(['State','City','zip_code']).apply(lambda x: category_frequency_func(x,False))
category_count = category_count.rename(columns={'cat_frequency':'cat_count'})
category_count.index = category_count.index.droplevel(3)
category_count.head()

venue_category  cat_count  rank
State   City       zip_code                                      
Alabama Birmingham 35203             Coffee Shop          3     1
                   35203     Fried Chicken Joint          3     2
                   35203                   Hotel          3     3
                   35203                 Theater          2     4
                   35203      Chinese Restaurant          2     5

**Compute measure**

In [229]:
# Dictionary with total population by zip
zip_population = acs_features['total_population'].to_dict()

# Get number of venues per 1000 people
category_count['zip_population'] = [zip_population.get(zipcode) for zipcode in category_count.index.get_level_values(2)]
category_count['category_per_1000'] = (category_count['cat_count']*1000/category_count['zip_population']).round(4)
category_count

venue_category  cat_count  rank  \
State     City       zip_code                                            
Alabama   Birmingham 35203                Coffee Shop          3     1   
                     35203        Fried Chicken Joint          3     2   
                     35203                      Hotel          3     3   
                     35203                    Theater          2     4   
                     35203         Chinese Restaurant          2     5   
...                                               ...        ...   ...   
Wisconsin Milwaukee  53233     Furniture / Home Store          1    41   
                     53233                Karaoke Bar          1    42   
                     53233         Chinese Restaurant          1    43   
                     53233        Monument / Landmark          1    44   
                     53233             Discount Store          1    45   

                               zip_population  category_per_1000  
State     City       zip_code                                     
Alabama   Birmingham 35203               3151             0.9521  
                     35203               3151             0.9521  
                     35203               3151             0.9521  
                     35203               3151             0.6347  
                     35203               3151             0.6347  
...                                       ...                ...  
Wisconsin Milwaukee  53233              15376             0.0650  
                     53233              15376             0.0650  
                     53233              15376             0.0650  
                     53233              15376             0.0650  
                     53233              15376             0.0650  

[99708 rows x 5 columns]

#### Venue Category Frequency Matrix - Population-Zip Relative

In [230]:
category_per1000_matrix = category_count.reset_index().pivot('zip_code','venue_category','category_per_1000').fillna(0)
category_per1000_matrix.head()

venue_category     ATM  Acai House  Accessories Store  Acupuncturist  \
zip_code                                                               
01103           0.0000         0.0                0.0            0.0   
01104           0.0000         0.0                0.0            0.0   
01105           0.0000         0.0                0.0            0.0   
01107           0.0000         0.0                0.0            0.0   
01108           0.0346         0.0                0.0            0.0   

venue_category  Adult Boutique  Advertising Agency  Afghan Restaurant  \
zip_code                                                                
01103                      0.0                 0.0                0.0   
01104                      0.0                 0.0                0.0   
01105                      0.0                 0.0                0.0   
01107                      0.0                 0.0                0.0   
01108                      0.0                 0.0                0.0   

venue_category  African Restaurant  Airport  Airport Food Court  ...  \
zip_code                                                         ...   
01103                          0.0      0.0                 0.0  ...   
01104                          0.0      0.0                 0.0  ...   
01105                          0.0      0.0                 0.0  ...   
01107                          0.0      0.0                 0.0  ...   
01108                          0.0      0.0                 0.0  ...   

venue_category  Whisky Bar  Wine Bar  Wine Shop  Winery  Wings Joint  \
zip_code                                                               
01103                  0.0       0.0        0.0     0.0          0.0   
01104                  0.0       0.0        0.0     0.0          0.0   
01105                  0.0       0.0        0.0     0.0          0.0   
01107                  0.0       0.0        0.0     0.0          0.0   
01108                  0.0       0.0        0.0     0.0          0.0   

venue_category  Women's Store  Xinjiang Restaurant  Yoga Studio  Zoo  \
zip_code                                                               
01103                     0.0                  0.0          0.0  0.0   
01104                     0.0                  0.0          0.0  0.0   
01105                     0.0                  0.0          0.0  0.0   
01107                     0.0                  0.0          0.0  0.0   
01108                     0.0                  0.0          0.0  0.0   

venue_category  Zoo Exhibit  
zip_code                     
01103                   0.0  
01104                   0.0  
01105                   0.0  
01107                   0.0  
01108                   0.0  

[5 rows x 645 columns]

### Venue Stats Table 

In [232]:
venue_stats = category_count[['category_per_1000','rank','venue_category']].copy()
venue_stats['cat_frequency'] = category_frequencies['cat_frequency']
venue_stats.head()

category_per_1000  rank       venue_category  \
State   City       zip_code                                                 
Alabama Birmingham 35203                0.9521     1          Coffee Shop   
                   35203                0.9521     2  Fried Chicken Joint   
                   35203                0.9521     3                Hotel   
                   35203                0.6347     4              Theater   
                   35203                0.6347     5   Chinese Restaurant   

                             cat_frequency  
State   City       zip_code                 
Alabama Birmingham 35203          0.057692  
                   35203          0.057692  
                   35203          0.057692  
                   35203          0.038462  
                   35203          0.038462

### City Data Features

In [18]:
# Select feature columns from city data
city_data['key'] = city_data['State'] + '_' + city_data['City']
city_data_features =  city_data.set_index('key')[['city_pop_chg_pcnt','city_pop_sqmi']] 
city_data_features = city_data_features.drop_duplicates()
city_data_features.head()

city_pop_chg_pcnt  city_pop_sqmi
key                                                        
New York_New York                       2.82          27012
California_Los Angeles                  2.42           8092
Illinois_Chicago                        0.86          11842
Texas_Houston                           4.55           3501
Pennsylvania_Philadelphia               1.78          11379

### Zip Attributes

In [312]:
zip_attributes = venues_cities[['zip_code','zip_latitude','zip_longitude','City','State']].copy()
zip_attributes = zip_attributes.drop_duplicates(subset='zip_code')
zip_attributes = zip_attributes.set_index('zip_code')
print('Number of rows: ',len(zip_attributes))
zip_attributes.head()

Number of rows:  3488


zip_latitude  zip_longitude      City     State
zip_code                                                 
10012        40.725960      -73.99834  New York  New York
10039        40.826181      -73.93710  New York  New York
10040        40.858704      -73.92853  New York  New York
10017        40.752159      -73.97231  New York  New York
10162        40.769334      -73.94893  New York  New York

## Merge Data

In [245]:
# Filter acs_features zips only to those in zip attributes for most populous 100 cities 
acs_features = acs_features[acs_features.index.isin(zip_attributes.index)]
print('Number of Zips:', len(acs_features))

Number of Zips: 3488


In [285]:
# Frequency Relative Category Pivot
frequency_pivot = venue_stats.reset_index().pivot('zip_code', columns='venue_category',values='cat_frequency')

# Rename columns
frequency_pivot.columns = [str(name) + '_freq' for name in frequency_pivot.columns]
frequency_pivot = frequency_pivot.fillna(0)

# Pop Relative Category Pivot
pop_relative = venue_stats.reset_index().pivot('zip_code', columns='venue_category',values='category_per_1000')

# Rename columns
pop_relative.columns = [str(name) + '_per1000' for name in pop_relative.columns]
pop_relative = pop_relative.fillna(0)

# Join both dataframes together to create universal feature table
venue_features = pop_relative.join(frequency_pivot)
venue_features.head()

ATM_per1000  Acai House_per1000  Accessories Store_per1000  \
zip_code                                                               
01103          0.0000                 0.0                        0.0   
01104          0.0000                 0.0                        0.0   
01105          0.0000                 0.0                        0.0   
01107          0.0000                 0.0                        0.0   
01108          0.0346                 0.0                        0.0   

          Acupuncturist_per1000  Adult Boutique_per1000  \
zip_code                                                  
01103                       0.0                     0.0   
01104                       0.0                     0.0   
01105                       0.0                     0.0   
01107                       0.0                     0.0   
01108                       0.0                     0.0   

          Advertising Agency_per1000  Afghan Restaurant_per1000  \
zip_code                                                          
01103                            0.0                        0.0   
01104                            0.0                        0.0   
01105                            0.0                        0.0   
01107                            0.0                        0.0   
01108                            0.0                        0.0   

          African Restaurant_per1000  Airport_per1000  \
zip_code                                                
01103                            0.0              0.0   
01104                            0.0              0.0   
01105                            0.0              0.0   
01107                            0.0              0.0   
01108                            0.0              0.0   

          Airport Food Court_per1000  ...  Whisky Bar_freq  Wine Bar_freq  \
zip_code                              ...                                   
01103                            0.0  ...              0.0            0.0   
01104                            0.0  ...              0.0            0.0   
01105                            0.0  ...              0.0            0.0   
01107                            0.0  ...              0.0            0.0   
01108                            0.0  ...              0.0            0.0   

          Wine Shop_freq  Winery_freq  Wings Joint_freq  Women's Store_freq  \
zip_code                                                                      
01103                0.0          0.0               0.0                 0.0   
01104                0.0          0.0               0.0                 0.0   
01105                0.0          0.0               0.0                 0.0   
01107                0.0          0.0               0.0                 0.0   
01108                0.0          0.0               0.0                 0.0   

          Xinjiang Restaurant_freq  Yoga Studio_freq  Zoo_freq  \
zip_code                                                         
01103                          0.0               0.0       0.0   
01104                          0.0               0.0       0.0   
01105                          0.0               0.0       0.0   
01107                          0.0               0.0       0.0   
01108                          0.0               0.0       0.0   

          Zoo Exhibit_freq  
zip_code                    
01103                  0.0  
01104                  0.0  
01105                  0.0  
01107                  0.0  
01108                  0.0  

[5 rows x 1290 columns]

**Now that we have a dataframe containing the measures of interest for each venue category by zip, we will filter them to only selected categories of interest for clustering.**

In [286]:
category_to_analyze = 'Beer Venue'

selected_columns = venue_features.columns[venue_features.columns.str.contains(category_to_analyze)]

selected_venue_features = venue_features[selected_columns]

In [287]:
selected_venue_features

Beer Venue_per1000  Beer Venue_freq
zip_code                                     
01103                 0.0000         0.000000
01104                 0.0000         0.000000
01105                 0.0000         0.000000
01107                 0.0000         0.000000
01108                 0.0000         0.000000
...                      ...              ...
99513                 0.0000         0.000000
99515                 0.0000         0.000000
99516                 0.0000         0.000000
99517                 0.0000         0.000000
99518                 0.0992         0.021277

[3488 rows x 2 columns]

### Merged Feature Table

In [319]:
# ACS features with selected venue
features = acs_features.join(selected_venue_features,how='left')

# ###### Create Numb of industrial establishment per 1000 people #######
features = features.drop(columns=['total_population','num_industrial_estab'])
features

Estimate!!INCOME AND BENEFITS (IN 2018 INFLATION-ADJUSTED DOLLARS)!!Total households!!Median household income (dollars)  \
zip_code                                                                                                                            
01609                                               42903.0                                                                         
01103                                               16720.0                                                                         
01107                                               26772.0                                                                         
01119                                               47439.0                                                                         
01108                                               38499.0                                                                         
...                                                     ...                                                                         
59102                                               54678.0                                                                         
62701                                               18618.0                                                                         
61602                                               20707.0                                                                         
61604                                               44943.0                                                                         
61614                                               60264.0                                                                         

          Estimate!!COMMUTING TO WORK!!Workers 16 years and over!!Mean travel time to work (minutes)  \
zip_code                                                                                               
01609                                                  23.9                                            
01103                                                  16.7                                            
01107                                                  23.6                                            
01119                                                  20.1                                            
01108                                                  22.2                                            
...                                                     ...                                            
59102                                                  15.3                                            
62701                                                  17.8                                            
61602                                                  16.2                                            
61604                                                  18.5                                            
61614                                                  16.9                                            

          Percent Estimate!!EMPLOYMENT STATUS!!Civilian labor force!!Unemployment Rate  \
zip_code                                                                                 
01609                                                   7.7                              
01103                                                  13.3                              
01107                                                  22.7                              
01119                                                  10.1                              
01108                                                  10.4                              
...                                                     ...                              
59102                                                   2.6                              
62701                                                   5.3                              
61602                      

## Feature Scaling

In [320]:
# Standard Scaler
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
features_scaled = scaler.fit_transform(features)

# Cluster Zips

In [323]:
# set number of clusters
kclusters = 4

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=42).fit(features_scaled)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:50] 

array([1, 3, 3, 3, 3, 2, 3, 2, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 2, 2, 2, 3,
       3, 2, 2, 1, 3, 2, 1, 0, 1, 3, 1, 2, 3, 2, 0, 3, 1, 3, 1, 1, 3, 1,
       1, 1, 3, 1, 1, 1], dtype=int32)

In [324]:
# Number of clusters
len(kmeans.labels_)

3488

## Add cluster labels to Zip attributes

In [325]:
# ZIP DATA
labels_df = pd.DataFrame(features.index,columns=['zip_code'])
labels_df['cluster'] = kmeans.labels_
labels_dict = labels_df.set_index('zip_code').to_dict()['cluster']

In [326]:
zip_attributes['cluster'] = [labels_dict.get(key) for key in zip_attributes.index]
zip_attributes = zip_attributes.dropna()

# Convert cluster labes to int
zip_attributes['cluster'] = zip_attributes['cluster'].astype(int)
zip_attributes.head()

zip_latitude  zip_longitude      City     State  cluster
zip_code                                                          
10012        40.725960      -73.99834  New York  New York        1
10039        40.826181      -73.93710  New York  New York        3
10040        40.858704      -73.92853  New York  New York        1
10017        40.752159      -73.97231  New York  New York        1
10162        40.769334      -73.94893  New York  New York        1

In [46]:
# CITY DATA
#city_attributes =  city_data.set_index('key')[['City',
#                                                   'State',
#                                               'city_latitude',
#                                               'city_longitude']] 
#city_attributes = city_attributes.rename(columns={'city_latitude':'city_longitude','city_longitude':'city_latitude'})
#
#city_attributes = city_attributes.drop_duplicates()
#city_attributes['cluster'] = kmeans.labels_
#
## Convert cluster labes to int
#city_attributes['cluster'] = city_attributes['cluster'].astype(int)
#city_attributes

## Visualize Results

In [327]:
latitude = 37.0902
longitude = -95.7129

# create map of US using latitude and longitude values
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=3)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(zip_attributes['zip_latitude'], 
                                  zip_attributes['zip_longitude'], 
                                  zip_attributes['City'], 
                                  zip_attributes['cluster']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [336]:
# Let's view the total number of zips per cluster
zip_attributes.join(features).groupby('cluster').count()

zip_latitude  zip_longitude  City  State  \
cluster                                             
0                 124            124   124    124   
1                 430            430   430    430   
2                1639           1639  1639   1639   
3                1295           1295  1295   1295   

         Estimate!!INCOME AND BENEFITS (IN 2018 INFLATION-ADJUSTED DOLLARS)!!Total households!!Median household income (dollars)  \
cluster                                                                                                                            
0                                                      124                                                                         
1                                                      430                                                                         
2                                                     1639                                                                         
3                                                     1295                                                                         

         Estimate!!COMMUTING TO WORK!!Workers 16 years and over!!Mean travel time to work (minutes)  \
cluster                                                                                               
0                                                      124                                            
1                                                      430                                            
2                                                     1639                                            
3                                                     1295                                            

         Percent Estimate!!EMPLOYMENT STATUS!!Civilian labor force!!Unemployment Rate  \
cluster                                                                                 
0                                                      124                              
1                                                      430                              
2                                                     1639                              
3                                                     1295                              

         Estimate!!GROSS RENT!!Occupied units paying rent!!Median (dollars)  \
cluster                                                                       
0                                                      124                    
1                                                      430                    
2                                                     1639                    
3                                                     1295                    

         Percent Estimate!!SEX AND AGE!!Total population!!Male  \
cluster                                                          
0                                                      124       
1                                                      430       
2                                                     1639       
3                                                     1295       

         Percent Estimate!!SEX AND AGE!!Total population!!Female  ...  \
cluster                                                           ...   
0                                                      124        ...   
1                                                      430        ...   
2                                                     1639        ...   
3                                                     1295        ...   

         Percent Estimate!!EDUCATIONAL ATTAINMENT!!Population 25 years and over!!Associate's degree  \
cluster                                                                                               
0                                                      124                                            
1                                                      430                                            
2                   

# Analyze Clusters 

In [338]:
# Check mean of variables per cluster
all_data = zip_attributes.join(features)
all_data = all_data.groupby('cluster').mean().round(2).transpose()
qgrid.show_grid(all_data)

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…